Scrape School Addresses
=======================

Try to find more accurate addresses from the school websites.


In [3]:

from requests import Session
import requests
import pandas as pd

from nycschools import schools, geo, ui
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim
from shapely.geometry import Point

import geopandas as gpd
import folium
from geopy.extra.rate_limiter import RateLimiter
from geopy.geocoders import GoogleV3
from concurrent.futures import ThreadPoolExecutor, as_completed
import overpy


In [25]:
buildings = "https://data.cityofnewyork.us/api/geospatial/nqwf-w8eh?method=export&format=GeoJSON"
foot = gpd.read_file(buildings)
foot

name    base_bbl shape_area   heightroof  mpluto_bbl cnstrct_yr  \
0        None  3065220021        0.0  29.74985318  3065220021       1925   
1        None  5012640036        0.0        22.63  5012640036       1965   
2        None  5060190091        0.0        35.76  5060190091       1970   
3        None  3086910048        0.0         37.5  3086910048       1928   
4        None  4075020005        0.0  18.01511294  4075020005       1950   
...       ...         ...        ...          ...         ...        ...   
1115121  None  2032580130       None        25.66  2032580130       1960   
1115122  None  2030370077       None        67.19  2030370077       1912   
1115123  None  5014850128       None        24.26  5014850128       1970   
1115124  None  5040700093       None        21.76  5040700093       1986   
1115125  None  4092260053       None        37.43  4092260053       1910   

                                       globalid   lststatype feat_code  \
0        {31298F86-3088-4F53-B3DB-71A9EFA6FA1F}  Constructed      2100   
1        {F5F8CDA5-69E2-46F8-8F69-BA95C025B520}  Constructed      2100   
2        {9F644794-F72C-4582-9E5E-B337E2B97068}  Constructed      2100   
3        {F916B22D-E25B-44AE-9FA9-2A51191B9CDF}  Constructed      2100   
4        {525F2C24-616B-4F29-98A3-8FEA5D4B1A7D}  Constructed      2100   
...                                         ...          ...       ...   
1115121  {B2510231-D1E2-4F2C-9730-0A5A0A009D8B}  Constructed      2100   
1115122  {F2D8EA0C-EA1A-48D3-AE68-D805FF79DB04}  Constructed      2100   
1115123  {D9B546C4-881E-4E31-99C5-45F92ECB6531}  Constructed      2100   
1115124  {0E3612F3-7D91-468D-BA2C-FF497E35DFF3}  Constructed      2100   
1115125  {30656C78-2910-4341-9A8B-AF695B6DCBAF}  Constructed      2100   

        groundelev  geomsource      bin lstmoddate doitt_id shape_len  \
0               40  Photogramm  3170958 2017-08-22    96807       0.0   
1               39  Photogramm  5028452 2017-08-22   326368       0.0   
2               51  Photogramm  5078368 2017-08-22   746627       0.0   
3                6  Photogramm  3245111 2017-08-22   786626       0.0   
4               93  Photogramm  4161096 2017-08-22   746409       0.0   
...            ...         ...      ...        ...      ...       ...   
1115121         67  Photogramm  2015832 2017-08-22   323109      None   
1115122         77  Photogramm  2011324 2017-08-22   189363      None   
1115123         33  Photogramm  5029482 2017-08-22   798994      None   
1115124         11  Photogramm  5056626 2017-08-22   534113      None   
1115125         56  Photogramm  4192686 2017-08-22   173308      None   

                                                  geometry  
0        MULTIPOLYGON (((-73.96665 40.62600, -73.96685 ...  
1        MULTIPOLYGON (((-74.16790 40.63936, -74.16790 ...  
2        MULTIPOLYGON (((-74.19511 40.55611, -74.19520 ...  
3        MULTIPOLYGON (((-73.96113 40.57744, -73.96115 ...  
4        MULTIPOLYGON (((-73.75422 40.75591, -73.75417 ...  
...                                                    ...  
1115121                         POINT (-73.89813 40.88207)  
1115122                         POINT (-73.89457 40.85378)  
1115123                         POINT (-74.14960 40.61898)  
1115124                         POINT (-74.10674 40.56038)  
1115125                         POINT (-73.83622 40.69900)  

[1115126 rows x 16 columns]

In [26]:
foot.to_file("nyc-building-footprints.geojson", driver='GeoJSON')

In [28]:
# df = gpd.read_file("nyc-building-footprints.geojson")
# df.head()
# save foot as geopackage
foot.to_file("nyc-building-footprints.gpkg", driver='GPKG')


In [68]:
df = gpd.read_file("nyc-building-footprints.gpkg")
df.head()



name    base_bbl shape_area   heightroof  mpluto_bbl cnstrct_yr  \
0  None  3065220021        0.0  29.74985318  3065220021       1925   
1  None  5012640036        0.0        22.63  5012640036       1965   
2  None  5060190091        0.0        35.76  5060190091       1970   
3  None  3086910048        0.0         37.5  3086910048       1928   
4  None  4075020005        0.0  18.01511294  4075020005       1950   

                                 globalid   lststatype feat_code groundelev  \
0  {31298F86-3088-4F53-B3DB-71A9EFA6FA1F}  Constructed      2100         40   
1  {F5F8CDA5-69E2-46F8-8F69-BA95C025B520}  Constructed      2100         39   
2  {9F644794-F72C-4582-9E5E-B337E2B97068}  Constructed      2100         51   
3  {F916B22D-E25B-44AE-9FA9-2A51191B9CDF}  Constructed      2100          6   
4  {525F2C24-616B-4F29-98A3-8FEA5D4B1A7D}  Constructed      2100         93   

   geomsource      bin lstmoddate doitt_id shape_len  \
0  Photogramm  3170958 2017-08-22    96807       0.0   
1  Photogramm  5028452 2017-08-22   326368       0.0   
2  Photogramm  5078368 2017-08-22   746627       0.0   
3  Photogramm  3245111 2017-08-22   786626       0.0   
4  Photogramm  4161096 2017-08-22   746409       0.0   

                                            geometry  
0  MULTIPOLYGON (((-73.96665 40.62600, -73.96685 ...  
1  MULTIPOLYGON (((-74.16790 40.63936, -74.16790 ...  
2  MULTIPOLYGON (((-74.19511 40.55611, -74.19520 ...  
3  MULTIPOLYGON (((-73.96113 40.57744, -73.96115 ...  
4  MULTIPOLYGON (((-73.75422 40.75591, -73.75417 ...

In [76]:
# school_loc = geo.load_school_locations()
# school_loc = pd.read_csv("https://data.cityofnewyork.us/resource/a3nt-yts4.geojson?$limit=1000000")
# print(sorted(school_loc.columns))
# print(sorted(foot.columns))
# school_loc.location_code.isin(foot.globalid)
# school_loc[school_loc.location_code.isin(foot.globalid)]
import math
parts = 32
size = math.ceil(len(foot) / parts)
for i in range(parts):
    start = i * size
    end = start + size
    if end >= len(foot):
        part = foot.iloc[start:]
    else:
        part = foot.iloc[start:end]
    part.to_file(f"./footprints/nyc-building-footprints-{(i+1):02}.gpkg", driver='GPKG')

In [78]:
def read_part(i):
    return gpd.read_file(f"./footprints/nyc-building-footprints-{i:02}.gpkg")

def read_building_footprints():
    """Read the NYC footprints from local data files."""
    
    parts = []
    with ThreadPoolExecutor(max_workers=32) as executor:
        # Map the make_request function to all URLs
        dbn_futures = {executor.submit(read_part, i) for i in range(1, 33)}
        for future in as_completed(dbn_futures):
            parts.append(future.result())

    return pd.concat(parts)


foo = read_building_footprints()
print(len(foo), len(foot))

1115126 1115126


In [79]:
x = gpd.read_file(f"./footprints/nyc-building-footprints-01.gpkg")
len(x)

34848

In [67]:
# merge footprints on bbl
from nycschools import datasets
url = datasets.urls["school_geo"]["url"]
# url = "https://data.cityofnewyork.us/resource/a3nt-yts4.geojson?$limit=1000000"
school_loc = gpd.read_file(url)
# school_loc.head()
foot["bbl"] = foot.base_bbl.astype(str)
foot.mpluto_bbl = foot.mpluto_bbl.astype(str)
school_loc.bbl = school_loc.bbl.astype(str)
school_loc.bbl = school_loc.bbl.str.replace(".0", "")
# school_foot = foot.merge(school_loc[["dbn","bbl"]], on="bbl", how="inner")
# school_foot[['dbn', 'heightroof', 'shape_len', 'geometry']]
school_loc

xcoordinat           city    zip state loc_code boronum adimindist lcc  \
0        987390      MANHATTAN  10036    NY     M212       1          2   2   
1       1056968         QUEENS  11429    NY     Q034       4         29   2   
2       1000700       BROOKLYN  11203    NY     K091       3         17   2   
3        930477  STATEN ISLAND  10312    NY     R455       5         31   5   
4       1006407          BRONX  10451    NY     X522       2          7   5   
...         ...            ...    ...   ...      ...     ...        ...  ..   
1987     986852       BROOKLYN  11215    NY     K124       3         15   2   
1988    1033868         QUEENS  11419    NY     Q161       4         28   2   
1989    1022234          BRONX  10473    NY     X100       2          8   2   
1990     991316      MANHATTAN  10024    NY     M523       1         84  15   
1991    1049342         QUEENS  11412    NY     Q118       4         29   2   

             bbl ats_code ycoordinat primarybui                       address  \
0     1010380014   02M212     216649       M017           328 WEST  48 STREET   
1     4111510081   29Q034     198417       Q034  104-12 SPRINGFIELD BOULEVARD   
2     3047940026   17K091     180396       K091             532 ALBANY AVENUE   
3     5066130001   31R455     131756       R455              100 LUTEN AVENUE   
4     2024110022   07X522     237542       X600           333 EAST 151 STREET   
...          ...      ...        ...        ...                           ...   
1987  3010340001   15K124     182452       K124                  515 4 AVENUE   
1988  4094910001   28Q161     190873       Q161             101-33 124 STREET   
1989  2036410001   08X100     238985       X100             800 TAYLOR AVENUE   
1990  1012150001   84M523     225688       M470           145 WEST  84 STREET   
1991  4109260050   29Q118     195552       Q118               190-20 109 ROAD   

     managed_by      bin                                     loc_name  \
0             1  1025092                        P.S. 212 Midtown West   
1             1  4240503                        P.S. 034 John Harvard   
2             1  3106599            P.S. 091 The Albany Avenue School   
3             1  5082634                      Tottenville High School   
4             1  2001874        Bronx Design and Construction Academy   
...         ...      ...                                          ...   
1987          1  3023391                    P.S. 124 Silas B. Dutcher   
1988          1  4200748                  P.S. 161 Arthur Ashe School   
1989          1  2022550                        P.S. 100 Isaac Clason   
1990          2  1032128  Success Academy Charter School - Upper West   
1991          1  4233850                  P.S. 118 Lorraine Hansberry   

     geodistric                    geometry  
0             2  POINT (-73.98867 40.76133)  
1            29  POINT (-73.73770 40.71099)  
2            17  POINT (-73.94071 40.66181)  
3            31  POINT (-74.19343 40.52815)  
4             7  POINT (-73.91995 40.81865)  
...         ...                         ...  
1987         15  POINT (-73.99062 40.66746)  
1988         28  POINT (-73.82108 40.69044)  
1989          8  POINT (-73.86276 40.82255)  
1990          3  POINT (-73.97448 40.78613)  
1991         29  POINT (-73.76524 40.70318)  

[1992 rows x 18 columns]

In [22]:
# test local nominatim
nominatim_url = 'localhost'
geolocator = Nominatim(user_agent="nycschools", timeout=10, scheme='http', domain=nominatim_url)
coords = (40.6916404, -73.991543)
# Use the geolocator to perform reverse geocoding
# location = geolocator.reverse(coords)

# Print the address
# print(location.address)
address = "179 Livingston Street, Brooklyn, NY 11201"
location = geolocator.geocode(address)
coords = (location.latitude, location.longitude)


qry = f"http://localhost/reverse?lat={coords[0]}&lon={coords[1]}&format=json"

# print(qry)
# requests.get(qry).json()

response = requests.get('http://localhost/search', params={'q': address, 'format': 'json'})
print(response.url)
response.json()

http://localhost/search?q=179+Livingston+Street%2C+Brooklyn%2C+NY+11201&format=json


[{'place_id': 319888656,
  'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
  'osm_type': 'way',
  'osm_id': 145079141,
  'boundingbox': ['40.6915966', '40.6921528', '-73.9934332', '-73.9914484'],
  'lat': '40.6916404',
  'lon': '-73.991543',
  'display_name': 'Livingston Street, Cobble Hill, Brooklyn, Kings County, City of New York, New York, 11217, United States',
  'class': 'highway',
  'type': 'residential',
  'importance': 0.41001},
 {'place_id': 319882592,
  'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
  'osm_type': 'way',
  'osm_id': 5680631,
  'boundingbox': ['40.6873136', '40.6875285', '-73.9803588', '-73.9798126'],
  'lat': '40.6874103',
  'lon': '-73.9800584',
  'display_name': 'Livingston Street, Downtown Brooklyn, Kings County, City of New York, New York, 11217, United States',
  'class': 'highway',
  'type': 'residential',
  'importance': 0.40001}]

In [14]:

api = overpy.Overpass()
m = folium.Map(location=coords, zoom_start=16)

# add a point to the map at coords
folium.Marker(location=coords).add_to(m)

osm_ids = [2494203018]

for osm_id in osm_ids:
    query = f"""
    [out:json][timeout:25];
    way({osm_id});
    out body;
    >;
    out skel qt;
    """
    result = api.query(query)
    for way in result.ways:
        polygon = [[float(node.lat), float(node.lon)] for node in way.nodes]
        folium.Polygon(locations=polygon, color='blue', fill=True).add_to(m)

m

In [34]:
def get_building_shape(lat, lon):
    api = overpy.Overpass()
    query = f"""
    [out:json];
    way
      (around:7, {lat}, {lon})
      ["building"];
    (._;>;);
    out body;
    """
    result = api.query(query)
    # Process the result to extract building shape data
    # The processing part depends on how you want to use the shape data

    return result




# Use the coordinates obtained from step 1
r = get_building_shape(location.latitude, location.longitude)
r.ways

[<overpy.Way id=245112472 nodes=[2523610938, 2523610944, 2523611026, 9212421592, 2523610966, 2523610862, 2523610919, 2523610938]>]

In [122]:

df = schools.load_school_demographics()
df.dbn.nunique()
url = "https://www.schools.nyc.gov/schools/"
df["doe_url"] = df.dbn.apply(lambda x: url + x[2:])



In [134]:
results = []

def read_year(year, file):
    try:
        x = pd.read_csv(f"https://tools.nycenet.edu/vue-assets/static/data/sqs/{year}/{file}.csv")
        x["year"] = year
        return x
    except:
        print("no data,", year)
        return pd.DataFrame()

for year in range(2016, 2023):
    results.append(read_year(year, "school_info"))
    results.append(read_year(year, "school_info_pk"))


doe = pd.concat(results, axis=0)
doe.to_csv("doe_school_list.csv", index=False)

no data, 2016
no data, 2016
no data, 2017
no data, 2017
no data, 2018
no data, 2019
no data, 2020


In [16]:
def get_address(url, session):
    try:
        response = session.get(url)
        if response.status_code == 404:
            print(f"URL not found: {url}")
            return None
        html = response.text
        soup = BeautifulSoup(html, 'html.parser')
        address = None
        geo_district = None
        try:
            links = soup.select('a[href^="https://maps.google.com"]')
            address = links[0].text
        except:
            pass

        try:
            geo_district_tag = soup.find('strong', string='Geographic District:')
            geo_district = geo_district_tag.next_sibling.strip()
        except:
            pass

        return {"address": address, "latest_geo_district": geo_district}
    except Exception as e:
        return None



def fetch_all(dbns, max_workers=50):
    """Fetch data from a list of URLs in parallel using threading"""
    session = Session()
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        # Map the make_request function to all URLs
        dbn_futures = {executor.submit(get_address, f"https://www.schools.nyc.gov/schools/{dbn[2:]}", session): dbn for dbn in dbns}
        results = []
        for future in as_completed(dbn_futures):
            dbn = dbn_futures[future]
            try:
                # Retrieve the result
                data = future.result()
                data["dbn"] = dbn
                results.append(data)
            except Exception as e:
                print(f"Request to {url} generated an exception: {e}")

    return pd.DataFrame(results)
# results = fetch_all(data.dbn)


In [49]:
data = data.merge(results, on="dbn", how="left")
data

dbn          beds  district  geo_district       boro  \
0  01M015  310100010015         1             1  Manhattan   
1  01M019  310100010019         1             1  Manhattan   
2  01M020  310100010020         1             1  Manhattan   
3  01M034  310100010034         1             1  Manhattan   
4  01M063  310100010063         1             1  Manhattan   

                      school_name short_name    ay     year school_type  ...  \
0       P.S. 015 Roberto Clemente      PS 15  2016  2016-17   community  ...   
1             P.S. 019 Asher Levy      PS 19  2016  2016-17   community  ...   
2            P.S. 020 Anna Silver      PS 20  2016  2016-17   community  ...   
3  P.S. 034 Franklin D. Roosevelt      PS 34  2016  2016-17   community  ...   
4       The STAR Academy - P.S.63      PS 63  2016  2016-17   community  ...   

   ell_n  ell_pct  poverty_n  poverty_pct    eni               clean_name  \
0     12    0.067        152        0.854  0.882         roberto clemente   
1      9    0.033        207        0.764  0.578               asher levy   
2     93    0.172        315        0.583  0.677              anna silver   
3     27    0.077        336        0.960  0.862     franklin d roosevelt   
4      5    0.025        165        0.825  0.690  the star academy - ps63   

     zip                                   doe_url  \
0  10009  https://www.schools.nyc.gov/schools/M015   
1  10003  https://www.schools.nyc.gov/schools/M019   
2  10002  https://www.schools.nyc.gov/schools/M020   
3  10009  https://www.schools.nyc.gov/schools/M034   
4  10009  https://www.schools.nyc.gov/schools/M063   

                                    address  latest_geo_district  
0   333 East  4 Street, Manhattan, NY 10009                    1  
1                                       NaN                  NaN  
2     166 Essex Street, Manhattan, NY 10002                    1  
3  730 East  12 Street, Manhattan, NY 10009                    1  
4   121 East  3 Street, Manhattan, NY 10009                    1  

[5 rows x 55 columns]

In [ ]:

loc = geo


In [ ]:

df[["dbn","address"]].to_csv("school_addresses.csv", index=False)
demo = schools.load_school_demographics()
demo = demo[demo.ay == demo.ay.max()]

df = gpd.read_file("school_addresses.csv")
df = df.drop_duplicates()
demo["address"] = None
df = pd.concat([df, demo[["dbn", "address"]][~demo.dbn.isin(df.dbn)]])
df = df.merge(demo[["dbn","geo_district"]], on="dbn")
len(df)

In [43]:
# geolocation reverse lookup on address
data = df.copy()

nominatim_url = 'localhost'
geolocator = Nominatim(user_agent="nycschools", timeout=10, scheme='http', domain=nominatim_url)
def get_geometry(address):
    if not address or len(address) == 0:
        return None
    try:
        location = geolocator.geocode(address)
        if location:
            return Point(location.longitude, location.latitude)
        else:
            return None
    except Exception as e:
        print(f"Error: {address}")
        print(e)
        return None


# Apply the function to the address column
data['geometry'] = data['address'].apply(get_geometry)

In [47]:

# Convert the pandas DataFrame to a GeoDataFrame
gdf = gpd.GeoDataFrame(data, geometry='geometry', crs="EPSG:4326")
gdf.drop(columns=["geo_district"], inplace=True)
gdf.to_file("school_addresses.geojson", driver='GeoJSON')
gdf.dropna(subset=["geometry"], inplace=True)
gdf = gdf.merge(demo[["dbn","district", "beds", "school_name"]], on="dbn")
# gdf[["address","school_name","dbn"]].sort_values("address")
gdf.head()

dbn                                   address  \
0  01M015   333 East  4 Street, Manhattan, NY 10009   
1  01M020     166 Essex Street, Manhattan, NY 10002   
2  01M034  730 East  12 Street, Manhattan, NY 10009   
3  01M063   121 East  3 Street, Manhattan, NY 10009   
4  01M064   600 East  6 Street, Manhattan, NY 10009   

                     geometry  district          beds  \
0  POINT (-73.97874 40.72191)         1  310100010015   
1  POINT (-73.98640 40.72107)         1  310100010020   
2  POINT (-73.97507 40.72614)         1  310100010034   
3  POINT (-73.98626 40.72441)         1  310100010063   
4  POINT (-73.98176 40.72385)         1  310100010064   

                      school_name  
0       P.S. 015 Roberto Clemente  
1            P.S. 020 Anna Silver  
2  P.S. 034 Franklin D. Roosevelt  
3       The STAR Academy - P.S.63  
4           P.S. 064 Robert Simon

In [79]:
url_404 = []
url_other = []
error_log = []

def scrape_school(url, ay, session):
    """Load the JSON data for a single school from the nycenet snapshot unpublished API"""
   
    try:
        response = session.get(url)
        if response.status_code == 200:
            json = response.json()
            df = pd.DataFrame(json)
            df = df.pivot(index='dbn', columns='varname', values='value').reset_index()
            df.columns.name = None
            df["ay"] = ay
            return df
        if response.status_code == 404:
            url_404.append(url)
        else:
            url_other.append((url, response.status_code))

        return None
    except Exception as e:
        dbn = url.split("/")[-2]
        error_log.append((dbn, url, e))
        return None


def scrape_year(dbns, year, school_type, max_workers=50):
    """Fetch data from a list of URLs in parallel using threading
    Parameters
    ----------
    dbns : list the list of DBN school identifiers to scrape
    year : int the year, years are in the Spring of the academic year, it appears that data is available for 2016-2022
    school_type : str the type of school. Types:
                  - "EMS" for elementary/middle 
                  - "HS" for high school
                  - "D75" for District 75 schools
    max_workers : int the number of threads to use, default is 50

    Returns
    -------
    DataFrame the scraped data, combined into a single dataframe. 
              The data contains many null values as all schools 
              and all years are not consistent in the data they provide.
    """
    session = Session()
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        make_url = lambda dbn: f"https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/{year}/{dbn}/{school_type}"
        futures = [executor.submit(scrape_school, make_url(dbn), year - 1, session) for dbn in dbns]
        results = []
        for future in as_completed(futures):
            data = future.result()
            if data is not None:
                results.append(data)
    try:
        all = pd.concat(results, axis=0, ignore_index=True)
        return all
    except Exception as e:
        print(e)
        print(results)
        return pd.DataFrame()


def scrape_schools(data, school_type):
    years = range(2017, 2023)
    results = []
    for year in years:
        # print(f"Loading year {year}")
        tmp = data[data.ay == year - 1].copy()
        # print(f"looking for {len(tmp)} schools ({school_type})")
        dbns = tmp.dbn.unique()
        if len(dbns) == 0:
            continue
        results.append(scrape_year(dbns, year, school_type))
   
    if len(results) == 0:
        return None
    all = pd.concat(results, axis=0, ignore_index=True)
    return all

In [ ]:

print("NYCENET Lookup")

data = df.copy()
d75 = scrape_schools(data[data.district == 75], "D75")
ems = scrape_schools(data, "EMS")
hs = scrape_schools(data, "HS")
hst = scrape_schools(data, "HST")
ec = scrape_schools(data, "EC")
print("all done")

In [110]:

found = [(set(x.dbn.unique())) for x in [d75, ems, hs, hst, ec]]
found = set.union(*found)
found
missing = df[~df.dbn.isin(found)]
missing[['dbn', 'school_name','district','doe_url']]

dbn                                      school_name  district  \
88     02M391                          District 2 Pre-K Center         2   
325    07X533               Learning through Play Pre-K Center         7   
449    09X582    Garden of Learning and Discovery Pre-K Center         9   
530    10X535                           Rose Hill Pre-K Center        10   
591    11X534                         District 11 Pre-K Center        11   
...       ...                                              ...       ...   
10693  84R088       Staten Island Hebrew Public Charter School        84   
11081  84X637   Success Academy Charter School � Bronx 5 Lower        84   
11082  84X638   Success Academy Charter School � Bronx 5 Upper        84   
11083  84X639                  Dream Charter School Highbridge        84   
11084  84X640  Family Life Academy Charter Schools High School        84   

                                        doe_url  
88     https://www.schools.nyc.gov/schools/M391  
325    https://www.schools.nyc.gov/schools/X533  
449    https://www.schools.nyc.gov/schools/X582  
530    https://www.schools.nyc.gov/schools/X535  
591    https://www.schools.nyc.gov/schools/X534  
...                                         ...  
10693  https://www.schools.nyc.gov/schools/R088  
11081  https://www.schools.nyc.gov/schools/X637  
11082  https://www.schools.nyc.gov/schools/X638  
11083  https://www.schools.nyc.gov/schools/X639  
11084  https://www.schools.nyc.gov/schools/X640  

[176 rows x 4 columns]

In [112]:
for dbn, url, e in error_log:
    print(f"{dbn}: {url}")
    print(e)

# scrape_school("https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2022/84X587/D75", 2022, Session())
# recovered = scrape_schools(missing, "D75")
# recovered
# d75 = pd.concat([d75, recovered], axis=0, ignore_index=True)


75M501: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2017/75M501/D75
'dbn'
75M401: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2017/75M401/D75
'dbn'
75M401: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2019/75M401/D75
'dbn'
75M501: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2019/75M501/D75
'dbn'
75K231: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75K231/D75
'dbn'
75M501: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75M501/D75
'dbn'
75M401: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75M401/D75
'dbn'
75K036: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75K036/D75
'dbn'
75M501: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2021/75M501/D75
'dbn'
75K231: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2021/75K231/D75
'dbn'
75K036: https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2021/75K03

In [63]:




d75.to_csv("d75_snapshot.csv", index=False)
ems.to_csv("ems_snapshot.csv", index=False)
hs.to_csv("hs_snapshot.csv", index=False)
hst.to_csv("hst_snapshot.csv", index=False)

In [83]:
# missing[['dbn','ay', 'school_name','district','doe_url']]
for e in error:
    print(e)


('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2017/75M501/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2017/75M401/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2019/75M401/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2019/75M501/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75K036/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75M501/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75K231/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2020/75M401/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2021/75K036/D75', KeyError('dbn'))
('https://tools.nycenet.edu/api/v1/data/school/app/snapshot/all/2021/75M501/D75', KeyError('dbn'))
('https://

In [119]:
snapshot = pd.read_csv("school_snapshot.csv")
df = schools.load_school_demographics()

missing = df[~df.dbn.isin(snapshot.dbn.unique())]
missing

/tmp/ipykernel_44448/2382633607.py:1: DtypeWarning: Columns (4,5,7,8,9,10,11,12,13,14,15,17,18,19,20,21,22,23,24,25,26,27,28,29,30,36,37,41,44,61,62,63,64,65,66,68,69,70,71,72,73,74,75,92,93,94,95,96,135,136,137,138,139,140,141,142,143,144,145,146,147,148,154,155,156,157,158,159,160,161,171,172,173,174,175,176,177,178,179,180,181,185,189,190,191,192,193,194,195,196,197,198,199,200,201,202,205,206,207,208,209,210,212,213,214,215,216,217,218,219,220,221,222,223,224,225,226,227,228,229,230,231,232,233,235,236,237,238,239,240,242,243,244,245,246,247,248,249,264,265,266,267,280,281,282,283,284,285,286,287,288,289,291,292,293,299,304,309,314,319,324,329,334,342,344,345,346,347,358,359,360,361,362,363,364,365,366,371,372,373,374,375,376,377,378,379,380,381,382,383,384,385,386,387,388,389,390,391,392,393,394,395,396,397,398,399,400,401,402,403,404,405,406,407,408,409,410,411,412,413,414,415,416,417,418,419,420,421,422,423,424,425,426,427,428,429,430,431,432,433,434,435,436,437,438,439,440,441,

dbn          beds  district  geo_district       boro  \
1      01M019  310100010019         1             1  Manhattan   
12     01M292  310100011292         1             1  Manhattan   
19     01M448  310100011448         1             1  Manhattan   
21     01M458  310100011458         1             1  Manhattan   
22     01M515  310100011515         1             1  Manhattan   
...       ...           ...       ...           ...        ...   
11080  84X635             0        84             0      Bronx   
11081  84X637             0        84             0      Bronx   
11082  84X638             0        84             0      Bronx   
11083  84X639             0        84             0      Bronx   
11084  84X640             0        84             0      Bronx   

                                             school_name short_name    ay  \
1                                    P.S. 019 Asher Levy      PS 19  2016   
12                            Orchard Collegiate Academy     HS 292  2016   
19                   University Neighborhood High School     HS 448  2016   
21                             Forsyth Satellite Academy     HS 458  2016   
22               Lower East Side Preparatory High School     HS 515  2016   
...                                                  ...        ...   ...   
11080  Earl Monroe New Renaissance Basketball Charter...     HS 635  2022   
11081     Success Academy Charter School � Bronx 5 Lower     NA 637  2022   
11082     Success Academy Charter School � Bronx 5 Upper     PS 638  2022   
11083                    Dream Charter School Highbridge     NA 639  2022   
11084    Family Life Academy Charter Schools High School     NA 640  2022   

          year school_type  ...  missing_race_ethnicity_data_pct  swd_n  \
1      2016-17   community  ...                            0.000     88   
12     2016-17   community  ...                            0.007     38   
19     2016-17   community  ...                            0.000     58   
21     2016-17   community  ...                            0.000     45   
22     2016-17   community  ...                            0.000     30   
...        ...         ...  ...                              ...    ...   
11080  2022-23     charter  ...                            0.000     55   
11081  2022-23     charter  ...                            0.000      7   
11082  2022-23     charter  ...                            0.000      9   
11083  2022-23     charter  ...                            0.000     11   
11084  2022-23     charter  ...                            0.000     16   

        swd_pct  ell_n   ell_pct  poverty_n  poverty_pct       eni  \
1      0.325000      9  0.033000        207     0.764000  0.578000   
12     0.271000     20  0.143000        128     0.914000  0.847000   
19     0.148000     35  0.089000        351     0.895000  0.753000   
21     0.212000     11  0.052000        145     0.684000  0.649000   
22     0.054000    390  0.698000        186     0.333000  0.900000   
...         ...    ...       ...        ...          ...       ...   
11080  0.239130     12  0.052174        171     0.743478  0.780507   
11081  0.064220      5  0.045872         94     0.862385  0.927222   
11082  0.157895      3  0.052632         45     0.789474  0.856579   
11083  0.215686      3  0.058824         49     0.960000  0.902667   
11084  0.158416     15  0.148515         94     0.930693  0.926320   

                                              clean_name    zip  
1                                             asher levy  10003  
12                            orchard collegiate academy  10002  
19                   university neighborhood high school  10002  
21                             forsyth satellite academy  10002  
22               lower east side preparatory high school  10002  
...                                                  ...    ...  
11080  earl monroe new renaissance basketball charter...      0  
11081     success acad

In [121]:
len(df)

11120

In [97]:

common = set(results[0].columns)
union = set(common)
for f in results[1:]:
    cols = set(f.columns)
    union = union.union(cols)
    common = common.intersection(cols)

difference = union - common

# print(f"All: {union}")
# for c in sorted(difference): print(c)

pd.concat(results, axis=0)

dbn abbr_school_type              address all_es_admissionsmethods  \
0  01M034              K-8  730 East  12 Street                Non-Zoned   
0  01M134               ES    293 East Broadway                Non-Zoned   
0  01M184              K-8    327 Cherry Street                Non-Zoned   
0  01M020               ES     166 Essex Street                Non-Zoned   
0  01M110               ES   285 Delancy Street  District G&T, Non-Zoned   
0  01M140              K-8     123 Ridge Street                Non-Zoned   
0  01M064               ES   600 East  6 Street                Non-Zoned   
0  01M142               ES  100 Attorney Street                Non-Zoned   
0  01M063               ES   121 East  3 Street                Non-Zoned   
0  01M015               ES   333 East  4 Street  Non-Zoned, District G&T   

  all_ms_admissionsmethods attendance_rate authorizer_website  \
0                     Open             96%               None   
0                      NaN             97%               None   
0        Language Criteria             98%               None   
0                      NaN             96%               None   
0                      NaN             98%               None   
0                     Open             96%               None   
0                      NaN             97%               None   
0                      NaN             96%               None   
0                      NaN             97%               None   
0                      NaN             97%               None   

  cavg_attendance_inperson_k8_all cavg_attendance_k8_all  \
0                             94%                    90%   
0                             91%                    90%   
0                             94%                    90%   
0                             91%                    90%   
0                             91%                    90%   
0                             94%                    90%   
0                             91%                    90%   
0                             91%                    90%   
0                             91%                    90%   
0                             91%                    90%   

  cavg_attendance_remote_k8_all  ... t_q174_p_raw t_q23_p t_q23_p_raw  \
0                           94%  ...          NaN     NaN         NaN   
0                           92%  ...         0.92    0.53        0.53   
0                           94%  ...          NaN     NaN         NaN   
0                           92%  ...         0.97     0.9         0.9   
0                           92%  ...         0.95    0.87        0.87   
0                           94%  ...          NaN     NaN         NaN   
0                           92%  ...            1    0.94        0.94   
0                           92%  ...          0.9     0.9         0.9   
0                           92%  ...            1    0.84        0.84   
0                           92%  ...         0.96    0.92        0.92   

  val_ele_core_all val_prof_2plus_watn3_elalevel1  \
0              NaN                            NaN   
0              95%                            N/A   
0              NaN                            NaN   
0              96%                            N/A   
0              99%                            N/A   
0              NaN                            NaN   
0              92%                            N/A   
0              90%                            N/A   
0              99%                            N/A   
0              94%                            N/A   

  val_prof_2plus_watn3_mthlevel1 val_prof_pct_watn3_elalevel2  \
0                            NaN                          NaN   
0                            N/A                          N/A   
0                            NaN                          NaN   
0                            N/A                          N/A   
0                            N/A                          N/A   
0             